#Problem Set 3 - Algorithmic Perspective on Strongly Correlated Systems

##Problem 1 - More about Matrix Product States

*In this question, we are going to apply some of the ideas we've learned about matrix product states.* 

First, I'm going to write some code for you to define the matrix-product-state type.

In [62]:
using Iterators

function Print(i)
    println("$i")
end

type index
    index_dims ::  Array{Int64}
    index_names :: Array{ASCIIString}
end

type Tensor
    data :: Array{Float64}
    myIndex :: index
end

type MPS
    sites :: Array{Tensor}
    siteIndex ::  Array{Integer}
end

function MakeTensor(theIndex)
#    Tensor(Array(Float64,tuple(theIndex.index_dims[:]...)),theIndex)
    Tensor(rand(tuple(theIndex.index_dims[:]...)),theIndex)
end

D=5
spin_deg=2
mps_size=3

mps=MPS(
         vcat(vcat(
                   [MakeTensor(index([1,D,spin_deg],
                        ["end","i1","s1"]))],
                   [MakeTensor(index([D,D,spin_deg],
                        ["i$(i-1)","i$(i)","s$i"])) for i in 2:mps_size-1]),
              [MakeTensor(index([D,1,spin_deg],
                        ["i$(mps_size-1)","end","s$(mps_size)"]))]),
        [1:mps_size])

Print("MPS generated")


MPS generated


To get the number sites of a MPS can be done by evaluating

In [48]:
length(mps.sites)

3

To get the shape of the tensor on site 1 we can evaluate 

In [53]:
size(mps.sites[2].data)

(5,5,2)

and see we have a 5 x 5 x 2 tensor (we have defined things so that we have the last index as the physical dimension).  Therefore, if we want to see the matrix for spin up of the second site we get

In [54]:
mps.sites[2].data[:,:,1]

5x5 Array{Float64,2}:
 0.307225  0.562404   0.292506   0.831241   0.771663 
 0.757821  0.154662   0.595912   0.721375   0.943407 
 0.579584  0.0897524  0.0215561  0.622871   0.873655 
 0.151583  0.213178   0.123019   0.0410211  0.269327 
 0.375382  0.466739   0.804231   0.950838   0.0143469

Write some code to evaluate a particular configuration, say [1,2,1].

In [61]:
#here is your code you're writing to evaluate

function evaluate(config,mps)
    myResult=0
    return myResult
end
evaluate([1,2,1],mps)

0

Now, please write some code to compute the overlap of two matrix product states.

In [64]:
#here is your code you're writing to evaluate

function overlap(mps1,mps2)
    myResult=0
    return myResult
end
overlap(mps,mps)

0

##Problem 2 - Applying local H operators to MPS

*In this question, we are going to study how local Hermitian operators acting on a matrix-product states affects their bond dimension.*


Consider a matrix product state.  Suppose you apply a Hermitian operator 

$$H_i = \left(
\begin{array}{cc} 
 \alpha & \beta \\
 \beta^* & \gamma \end{array}  \right)
$$


which is applied locally on site $i$. 

When $H_i$ is applied to a Matrix product state of bond-dimension $D$, how does the state change?  What is the bond-dimension of the new MPS? Write a few lines of code that does it below.



In [66]:
function ApplyOneSiteH(H,i,mps)
    newUp=H[1,1]*mps.sites[i].data[:,:,1]+H[1,2]*mps.sites[i].data[:,:,2]
    newDown=H[2,1]*mps.sites[i].data[:,:,1]+H[2,2]*mps.sites[i].data[:,:,2]
    mps.sites[i].data[:,:,1]=newUp
    mps.sites[i].data[:,:,2]=newDown
end

ApplyOneSiteH (generic function with 1 method)

$\newcommand{zerodel}{.\kern-\nulldelimiterspace}$
$\newcommand{ket}[1]{\left| #1 \right\rangle}$
$\newcommand{bra}[1]{\left\langle #1 \right|}$
$\newcommand{braket}[2]{\left\langle #1 \right|\left| #2\right\rangle}$
$\newcommand{ketbra}[2]{\left| #1 \right\rangle\left\langle #2\right|}$
Suppose instead that we apply the Hermitian operator $H_i \otimes H_j$.  If the original bond-dimension of the MPS was $D$ what is the new bond-dimension?

For the next step, we want to consider the Schmidt decomposition of a Hermitian operator $H_{ij}$ which acts on the two adjacent states $i$ and $j$.  We could write out this operator as 

$$H=\sum_{abcd} \alpha_{abcd} \ketbra{ab}{cd}$$

Since we know how to schmidt-decompose a state, let us write the operator as a wave-function 
$$H = \sum_{(ac)(bd)} \alpha_{(ac)(bd)} \ket{(ac)}\ket{(bd)} $$ 
where the first bra acts on site 1 and the second bra acts on site 2 and we combine $(ac)$ into a single four-dimensional space (i.e. $\ket{00} \rightarrow \ket{0}, \ket{01} \rightarrow \ket{1},\ket{10} \rightarrow \ket{2},\ket{11} \rightarrow \ket{3})$.  Now, we can do a Schmdit decomposition on our state: 
$$H = \sum_j \beta_j \ket{L_j} \otimes \ket{R_j}.$$ 

Notice that $\ket{L_j}$ is a wave-function only on site $i$ in a Hilbert space of size 4 (i.e. it looks like $\alpha \ket{0} + \beta \ket{1} + \gamma \ket{2} + \delta \ket{3} $)  Rewriting this as an operator gives us 

$$O_i = \alpha \ketbra{0}{0} +\beta \ketbra{0}{1} + \gamma \ketbra{1}{0} + \delta \ketbra{1}
{1}$$ 

which acts on site $i$ as well as an operator $O_{i+1}$ which acts on site $i+1$.  This gives us 
$$H = \sum_j O^j_i \otimes O^j_{i+1}$$   We call this the schdmit decomposition of $H$.

* Show that applying $H$ in this Schmidt decomposed form is the same as applying the original $H$.

* What is the number of terms that can be in this sum?


In the next part of this question, let's think about the sum of two MPS $\ket{\Psi_1} + \ket{\Psi_2}$.  Write some code that produces a new MPS for this sum.  You can check your code by checking the amplitudes.  What is the maximal bond dimension of this new MPS?  Is it still canonical?  


In [40]:
function SumMPS(mps1,mps2)
    
end

[3.996787309153]


Using the above considerations, what is the maximal increase in bond-dimension for an application of $H_{ij}$ to adjacent sites $i$ and $j$ on the matrices on sites $i$ and $j$.  Does the application of $I_1 \otimes I_2 \otimes ... \otimes H_{ij} \otimes I_{j+1} \otimes ...$ change the bond-dimension of any state that is not $i$ and $j$.   If so, explain in what way?

## Problem 3 - Schmidt Decompositions

*In this question we'd like to understand how the entanglement rank over a cut on site $i$ bounds the entanglement rank over a cut on site $j$ where $|i-j|=a$*

**Notation:** A *cut* on site $i$ means a cut between sites $i$ and $i+1$.

Recall, that entanglement rank is the number of terms in the Schmidt Decomposition.

* First, show that if you are  are in mixed canonical form over site $i$ that the entanglement rank over site $i$ is bounded by the (right) bond-dimension at site $i$.

* Now, show as you change the MPS from a mixed canonical form over site $i$ to a mixed canonical form over site $j$, how much can the bond-dimension increase?

* Write code to take a MPS and make it mixed canonical over site $i$.  Test your results on some examples for the previous two parts.  *I may update this to make it more step by step if that is helpful*.  